In [1]:
import os
import warnings
import copy
import time

import numpy as np
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import *
import plotly.figure_factory as ff

from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import explained_variance_score, r2_score
from sklearn.linear_model import LinearRegression, Lasso, lasso_path, lars_path, LassoLarsIC
from sklearn.neural_network import MLPRegressor

os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' #Hide messy TensorFlow warnings
warnings.filterwarnings("ignore") #Hide messy Numpy warnings

import keras
from keras.layers.core import Dense, Activation, Dropout
from keras.layers import Input
from keras.models import Model

from keras.layers.recurrent import LSTM
from keras.regularizers import l1
from keras.models import Sequential
from keras.models import load_model

init_notebook_mode(connected=True)


Using TensorFlow backend.


In [2]:
# create a data set, sin wave plus random noise
nobs = 1000
x = np.linspace(0, 3*np.pi, num=nobs)
y = -np.cos(x) + x/(3*np.pi) + np.random.normal(0, 0.25, nobs)


In [3]:
# chart it

def mychart(*args):

    # pass some 2d n x 1 arrays, x, y, z
    
    # 1st array is independent vars
    # reshape to 1 dimensional array
    x = args[0].reshape(-1)
    
    # following are dependent vars plotted on y axis
    data = []
    for i in range(1, len(args)):
        data.append(Scatter(x=x,
                            y=args[i].reshape(-1),
                            mode = 'markers'))

    layout = Layout(
        yaxis=dict(
            autorange=True))
    
    fig = Figure(data=data, layout=layout)
    
    return iplot(fig, image='png') # png to save notebook w/static image   
    
mychart(x,y)

In [4]:
# fit with sklearn MLPRegressor

layer1_sizes=[1,2,3,4]
layer2_sizes=[1,2,3,4]
import itertools
from plotly import tools
                         
def run_grid(build_model_fn, layer1_sizes, layer2_sizes, x, y):
    nrows = len(layer1_sizes)
    ncols = len(layer2_sizes)
    
    hyperparameter_list = list(itertools.product(layer1_sizes, layer2_sizes))
    subplot_titles = ["%d units, %d units" % 
                      (layer1_size, layer2_size) for (layer1_size, layer2_size) in hyperparameter_list]
    
    fig = tools.make_subplots(rows=nrows, 
                              cols=ncols, 
                              subplot_titles=subplot_titles)
    
    for count, (layer1_size, layer2_size) in enumerate(hyperparameter_list):
        print("Layer 1 units: %d, Layer 2 units %d:" % (layer1_size, layer2_size))
        
        print("Running experiment %d of %d : %d %d" % (count+1, len(hyperparameter_list), layer1_size, layer2_size))
        model = build_model_fn(hidden_layer_sizes=(layer1_size, layer2_size),
                             max_iter=10000, tol=1e-8,
                             solver='lbfgs')
        x = x.reshape(-1,1)
        model.fit(x,y)
        z = model.predict(x)
        trace = Scatter(
            x = x.reshape(-1),
            y = z.reshape(-1),
            name = 'fit',    
            mode = 'markers',
            marker = dict(size = 2)
        )
        fig.append_trace(trace, count // nrows + 1, count % ncols +1)
    return(iplot(fig))
    
run_grid(MLPRegressor, layer1_sizes, layer2_sizes, x, y)

This is the format of your plot grid:
[ (1,1) x1,y1 ]    [ (1,2) x2,y2 ]    [ (1,3) x3,y3 ]    [ (1,4) x4,y4 ]  
[ (2,1) x5,y5 ]    [ (2,2) x6,y6 ]    [ (2,3) x7,y7 ]    [ (2,4) x8,y8 ]  
[ (3,1) x9,y9 ]    [ (3,2) x10,y10 ]  [ (3,3) x11,y11 ]  [ (3,4) x12,y12 ]
[ (4,1) x13,y13 ]  [ (4,2) x14,y14 ]  [ (4,3) x15,y15 ]  [ (4,4) x16,y16 ]

Layer 1 units: 1, Layer 2 units 1:
Running experiment 1 of 16 : 1 1
Layer 1 units: 1, Layer 2 units 2:
Running experiment 2 of 16 : 1 2
Layer 1 units: 1, Layer 2 units 3:
Running experiment 3 of 16 : 1 3
Layer 1 units: 1, Layer 2 units 4:
Running experiment 4 of 16 : 1 4
Layer 1 units: 2, Layer 2 units 1:
Running experiment 5 of 16 : 2 1
Layer 1 units: 2, Layer 2 units 2:
Running experiment 6 of 16 : 2 2
Layer 1 units: 2, Layer 2 units 3:
Running experiment 7 of 16 : 2 3
Layer 1 units: 2, Layer 2 units 4:
Running experiment 8 of 16 : 2 4
Layer 1 units: 3, Layer 2 units 1:
Running experiment 9 of 16 : 3 1
Layer 1 units: 3, Layer 2 units 2:
Running experi

In [5]:
# sklearn MLP regression didn't work well at all
# let's build our own keras model by wrappping it in sklearn interface

def build_ols_model(input_size = 1, hidden_layer_sizes=[4]):
    
    main_input = Input(shape=(input_size,), dtype='float32', name='main_input')

    lastlayer=main_input
    for layer_size in hidden_layer_sizes:
        lastlayer = Dense(layer_size, 
                          kernel_initializer=keras.initializers.glorot_normal(seed=None),
                          bias_initializer=keras.initializers.glorot_normal(seed=None),
                          activation='relu')(lastlayer)
    
    output = Dense(1, activation='linear')(lastlayer)
    
    model = Model(inputs=[main_input], outputs=[output])

    model.compile(loss="mean_squared_error", 
                  optimizer=keras.optimizers.Adam()
                 )
    print(model.summary())
    
    return model


    


In [6]:
EPOCHS=501
BATCH_SIZE=32
def run_experiment (model, x, y):
    
    models = []
    losses = []

    for epoch in range(EPOCHS):
        fit = model.fit(
            x,
            y,
            batch_size=BATCH_SIZE,
            epochs=1,
            verbose=0
        )
        
        train_loss = fit.history['loss'][-1]
            
        losses.append(train_loss)
        models.append(copy.copy(model))
        
        bestloss_index = np.argmin(losses)
        bestloss_value = losses[bestloss_index]
        if epoch % 10 == 0:
            print("%s Epoch %d of %d Loss %.6f Best Loss %.6f" % (time.strftime("%H:%M:%S"), 
                                                                  epoch, 
                                                                  EPOCHS, train_loss, 
                                                                  bestloss_value))
        # stop if loss rises by 20% from best
        if train_loss / bestloss_value > 1.2:
            print("%s Stopping..." % (time.strftime("%H:%M:%S")))
            break
            
    print ("%s Best training loss epoch %d, value %f" % (time.strftime("%H:%M:%S"), bestloss_index, bestloss_value))
    model = models[bestloss_index]
    
    train_score = model.evaluate(x, y)
    print(train_score)
    print("%s Train MSE: %.6f" % (time.strftime("%H:%M:%S"), train_score))
    print("%s Train R-squared: %.6f" % (time.strftime("%H:%M:%S"), 1-train_score/y.var()))

    return mychart(x, y, model.predict(x))


In [7]:
model = build_ols_model(hidden_layer_sizes=[16])
run_experiment(model, x, y)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
main_input (InputLayer)      (None, 1)                 0         
_________________________________________________________________
dense_1 (Dense)              (None, 16)                32        
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 17        
Total params: 49
Trainable params: 49
Non-trainable params: 0
_________________________________________________________________
None
11:44:23 Epoch 0 of 501 Loss 15.426664 Best Loss 15.426664
11:44:25 Epoch 10 of 501 Loss 0.509588 Best Loss 0.509588
11:44:26 Epoch 20 of 501 Loss 0.443615 Best Loss 0.443615
11:44:28 Epoch 30 of 501 Loss 0.441543 Best Loss 0.441543
11:44:30 Epoch 40 of 501 Loss 0.440950 Best Loss 0.440836
11:44:31 Epoch 50 of 501 Loss 0.440622 Best Loss 0.440603
11:44:33 Epoch 60 of 501 Loss 0.440766 Best Loss 0.44042

In [8]:
# wrap our keras model in sklearn wrapper so we can run grid like above MLPRegressor
from keras.wrappers.scikit_learn import KerasRegressor

# closure for sklearn wrapper
def make_build(layer_sizes):
    def myclosure():
        return build_ols_model(input_size=1, hidden_layer_sizes=layer_sizes)
    return myclosure

def make_keras_model(**kwargs):
    # make a function that takes hidden layer sizes kwarg and returns estimator of correct layer sizes
    build_fn = make_build(kwargs['hidden_layer_sizes'])

    keras_estimator = KerasRegressor(build_fn=build_fn, 
                                     nb_epoch=5000, 
                                     batch_size=32, 
                                     verbose=1)
    return keras_estimator
    
            


In [9]:
run_grid(make_keras_model, layer1_sizes, layer2_sizes, x, y)
# this also doesn't perform well
# takeaway: feedforward NN sucks for regression

This is the format of your plot grid:
[ (1,1) x1,y1 ]    [ (1,2) x2,y2 ]    [ (1,3) x3,y3 ]    [ (1,4) x4,y4 ]  
[ (2,1) x5,y5 ]    [ (2,2) x6,y6 ]    [ (2,3) x7,y7 ]    [ (2,4) x8,y8 ]  
[ (3,1) x9,y9 ]    [ (3,2) x10,y10 ]  [ (3,3) x11,y11 ]  [ (3,4) x12,y12 ]
[ (4,1) x13,y13 ]  [ (4,2) x14,y14 ]  [ (4,3) x15,y15 ]  [ (4,4) x16,y16 ]

Layer 1 units: 1, Layer 2 units 1:
Running experiment 1 of 16 : 1 1
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
main_input (InputLayer)      (None, 1)                 0         
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 2         
_________________________________________________________________
dense_4 (Dense)              (None, 1)                 2         
_________________________________________________________________
dense_5 (Dense)              (None, 1)                 2         

Epoch 1/1
1000/1000 [==============================] - 0s 106us/step
Layer 1 units: 3, Layer 2 units 1:
Running experiment 9 of 16 : 3 1
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
main_input (InputLayer)      (None, 1)                 0         
_________________________________________________________________
dense_27 (Dense)             (None, 3)                 6         
_________________________________________________________________
dense_28 (Dense)             (None, 1)                 4         
_________________________________________________________________
dense_29 (Dense)             (None, 1)                 2         
Total params: 12
Trainable params: 12
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/1
1000/1000 [==============================] - 0s 132us/step
Layer 1 units: 3, Layer 2 units 2:
Running experiment 10 of 16 : 3 

Epoch 1/1
1000/1000 [==============================] - 0s 192us/step


In [10]:
# try RandomForestRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import RandomizedSearchCV

rf = RandomForestRegressor(random_state = 42)
from pprint import pprint
# Look at parameters used by our current forest
print('Parameters currently in use:\n')
pprint(rf.get_params())

# First 2 are most important
# Number of trees in random forest
n_estimators = [int(a) for a in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(a) for a in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]

# Create the random grid
print("Search grid:")
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
pprint(random_grid)

Parameters currently in use:

{'bootstrap': True,
 'criterion': 'mse',
 'max_depth': None,
 'max_features': 'auto',
 'max_leaf_nodes': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 10,
 'n_jobs': 1,
 'oob_score': False,
 'random_state': 42,
 'verbose': 0,
 'warm_start': False}
Search grid:
{'bootstrap': [True, False],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'max_features': ['auto', 'sqrt'],
 'min_samples_leaf': [1, 2, 4],
 'min_samples_split': [2, 5, 10],
 'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]}


In [11]:
x.shape

(1000,)

In [12]:
x=x.reshape(x.shape[0],1)
y=y.reshape(y.shape[0],1)

In [13]:
rf = RandomForestRegressor()
rf.fit(x, y)
z = rf.predict(x)
mychart(x, y, z)

In [14]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestRegressor()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, 
                               param_distributions = random_grid, 
                               n_iter = 100, 
                               cv = 3, verbose=2, 
                               random_state=42, 
                               n_jobs = 1)
# Fit the random search model
rf_random.fit(x, y)



Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30 
[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30, total=   0.7s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30 


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s


[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30, total=   0.6s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30 
[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=400, max_features=sqrt, min_samples_split=5, max_depth=30, total=   0.6s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=10 
[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=10, total=   3.0s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=10 
[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=10, total=   2.6s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=10 
[CV]  bootstrap=True, min_sampl

[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=800, max_features=sqrt, min_samples_split=5, max_depth=90, total=   1.1s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10 
[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10, total=   3.2s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10 
[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10, total=   3.3s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10 
[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=2000, max_features=sqrt, min_samples_split=10, max_depth=10, total=   2.7s
[CV] bootstrap=False, min_samples_leaf=2, n_estimators=1600, max_features=sqrt, min_samples_split=5, max_depth=10 
[CV]  bootstrap

[CV]  bootstrap=True, min_samples_leaf=2, n_estimators=1800, max_features=auto, min_samples_split=2, max_depth=None, total=   2.2s
[CV] bootstrap=True, min_samples_leaf=2, n_estimators=1800, max_features=auto, min_samples_split=2, max_depth=None 
[CV]  bootstrap=True, min_samples_leaf=2, n_estimators=1800, max_features=auto, min_samples_split=2, max_depth=None, total=   2.4s
[CV] bootstrap=True, min_samples_leaf=2, n_estimators=1800, max_features=auto, min_samples_split=2, max_depth=None 
[CV]  bootstrap=True, min_samples_leaf=2, n_estimators=1800, max_features=auto, min_samples_split=2, max_depth=None, total=   2.6s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=1400, max_features=sqrt, min_samples_split=5, max_depth=80 
[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=1400, max_features=sqrt, min_samples_split=5, max_depth=80, total=   2.4s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=1400, max_features=sqrt, min_samples_split=5, max_depth=80 
[CV]  bootstrap

...

[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=1000, max_features=sqrt, min_samples_split=10, max_depth=80, total=   1.5s
[CV] bootstrap=False, min_samples_leaf=1, n_estimators=1000, max_features=sqrt, min_samples_split=10, max_depth=80 
[CV]  bootstrap=False, min_samples_leaf=1, n_estimators=1000, max_features=sqrt, min_samples_split=10, max_depth=80, total=   1.6s
[CV] bootstrap=False, min_samples_leaf=2, n_estimators=2000, max_features=auto, min_samples_split=10, max_depth=60 
[CV]  bootstrap=False, min_samples_leaf=2, n_estimators=2000, max_features=auto, min_samples_split=10, max_depth=60, total=   2.6s
[CV] bootstrap=False, min_samples_leaf=2, n_estimators=2000, max_features=auto, min_samples_split=10, max_depth=60 
[CV]  bootstrap=False, min_samples_leaf=2, n_estimators=2000, max_features=auto, min_samples_split=10, max_depth=60, total=   2.5s
[CV] bootstrap=False, min_samples_leaf=2, n_estimators=2000, max_features=auto, min_samples_split=10, max_depth=60 
[CV]  bootst

[CV]  bootstrap=True, min_samples_leaf=4, n_estimators=200, max_features=auto, min_samples_split=5, max_depth=80, total=   0.2s
[CV] bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60 
[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60, total=   2.5s
[CV] bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60 
[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60, total=   2.5s
[CV] bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60 
[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=auto, min_samples_split=2, max_depth=60, total=   2.8s
[CV] bootstrap=True, min_samples_leaf=2, n_estimators=600, max_features=auto, min_samples_split=10, max_depth=100 
[CV]  bootstrap=True, 

[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=None, total=   2.8s
[CV] bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=None 
[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=None, total=   2.5s
[CV] bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=None 
[CV]  bootstrap=False, min_samples_leaf=4, n_estimators=2000, max_features=sqrt, min_samples_split=5, max_depth=None, total=   2.5s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=800, max_features=sqrt, min_samples_split=5, max_depth=40 
[CV]  bootstrap=True, min_samples_leaf=1, n_estimators=800, max_features=sqrt, min_samples_split=5, max_depth=40, total=   1.0s
[CV] bootstrap=True, min_samples_leaf=1, n_estimators=800, max_features=sqrt, min_samples_split=5, max_depth=40 
[CV]  bootstrap=

[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:  8.3min finished


RandomizedSearchCV(cv=3, error_score='raise',
          estimator=RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
           oob_score=False, random_state=None, verbose=0, warm_start=False),
          fit_params=None, iid=True, n_iter=100, n_jobs=1,
          param_distributions={'bootstrap': [True, False], 'min_samples_leaf': [1, 2, 4], 'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000], 'min_samples_split': [2, 5, 10], 'max_features': ['auto', 'sqrt'], 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None]},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring=None, verbose=2)

In [15]:
rf_random.best_params_
{'bootstrap': True,
 'max_depth': 70,
 'max_features': 'auto',
 'min_samples_leaf': 4,
 'min_samples_split': 10,
 'n_estimators': 400}

{'bootstrap': True,
 'max_depth': 70,
 'max_features': 'auto',
 'min_samples_leaf': 4,
 'min_samples_split': 10,
 'n_estimators': 400}

In [16]:
rf = RandomForestRegressor(n_estimators=400,
                           max_features='auto',
                           max_depth=None,
                           min_samples_leaf=4,
                           min_samples_split=10,
                          )
rf.fit(x, y)
z = rf.predict(x)
mychart(x, y, z)

In [17]:
rf.predict(np.random.uniform(low=0, high=8, size=10).reshape(10,1))

array([-0.21986661,  1.40764951, -0.33172553,  1.40203883, -0.21986661,
       -0.31580421,  1.41862084,  0.06309863, -0.98201201,  0.57664036])

In [19]:
from scipy.interpolate import UnivariateSpline
spl = UnivariateSpline(x, y)
z = spl(x)
mychart(x, y, z)

In [21]:
spl.set_smoothing_factor(94.0)
print(spl.get_knots())
z = spl(x)
mychart(x, y, z)

[0.         2.35855304 4.71710609 7.07565913 9.42477796]


In [22]:
from sklearn.metrics import mean_squared_error

def spline_cv_test(smoothing_factor):
    kf = KFold(n_splits=5)
    errors = []
    for train_index, test_index in kf.split(x):
        x_train, x_test = x[train_index], x[test_index]
        y_train, y_test = y[train_index], y[test_index]
        spline = UnivariateSpline(x_train, y_train)
        spline.set_smoothing_factor(smoothing_factor)
        y_pred_test = spline(x_test)
        errors.append(mean_squared_error(y_test, y_pred_test))
        return np.mean(np.array(errors))

print(spline_cv_test(49.856))
for sf in np.linspace(10, 110, num=101):
    print(sf, spline_cv_test(sf))


6.323464248167933
(10.0, 29139241297.354435)
(11.0, 26888054192.5276)
(12.0, 12581312461.24114)
(13.0, 24138738188.133846)
(14.0, 21455551677.259903)
(15.0, 21259883710.04871)
(16.0, 14779297197.220016)
(17.0, 40916686239.17037)
(18.0, 54077792589.58279)
(19.0, 61307837703.81329)
(20.0, 56340536992.4181)
(21.0, 53787054058.36845)
(22.0, 72776037115.01947)
(23.0, 71210739948.9296)
(24.0, 82548803412.35509)
(25.0, 105362949489.5807)
(26.0, 109784451763.66956)
(27.0, 93579774593.80069)
(28.0, 63364078853.069275)
(29.0, 34356665411.262726)
(30.0, 85541570240.12613)
(31.0, 71614182736.32814)
(32.0, 55795395272.728874)
(33.0, 44100931744.258064)
(34.0, 1041856210.285058)
(35.0, 1033213576.8894588)
(36.0, 1025434996.7409288)
(37.0, 868639279.2679269)
(38.0, 810230666.0885332)
(39.0, 122286009.38749148)
(40.0, 1368250.6692457518)
(41.0, 21474652.06020119)
(42.0, 18006378.273677878)
(43.0, 81313.15991493732)
(44.0, 125723.38298874408)
(45.0, 56980.94063085092)
(46.0, 27695.0094338631)
(47.0, 71

In [23]:
from xgboost import XGBRegressor
from sklearn.model_selection import RandomizedSearchCV

import scipy.stats as st

xgbreg = XGBRegressor(nthreads=1)  

one_to_left = st.beta(10, 1)  
from_zero_positive = st.expon(0, 50)

param_grid = {
        'silent': [False],
        'max_depth': [6, 10, 15, 20],
        'learning_rate': [0.001, 0.01, 0.1, 0.2, 0,3],
        'subsample': [0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        'colsample_bytree': [0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        'colsample_bylevel': [0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        'min_child_weight': [0.5, 1.0, 3.0, 5.0, 7.0, 10.0],
        'gamma': [0, 0.25, 0.5, 1.0],
        'reg_lambda': [0.1, 1.0, 5.0, 10.0, 50.0, 100.0],
        'n_estimators': [100]}

params = {  
    "n_estimators": [10, 20, 40, 80, 160, 320, 640],
    "max_depth": [4, 8, 16, 32, 64, 128],
    "learning_rate": [0.05, 0.10, 0.15, 0.20, 0.25, 0.30, 0.35, 0.40, 0.45, 0.50],
    "colsample_bytree": [1.0, 0.99, 0.95, 0.90, 0.85, 0.80, 0.60],
    "subsample": [1.0, 0.99, 0.95, 0.90, 0.85, 0.80, 0.60],
    "gamma": [0, 1.0, 1.5, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0],
    'reg_alpha': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100],
    "min_child_weight": [10, 20, 30, 40, 50, 60, 70, 80, 90, 100],
}

gs = RandomizedSearchCV(xgbreg, params, n_jobs=1)  
gs.fit(x, y)  
gs.best_params_


{'colsample_bytree': 1.0,
 'gamma': 1.0,
 'learning_rate': 0.2,
 'max_depth': 64,
 'min_child_weight': 30,
 'n_estimators': 10,
 'reg_alpha': 70,
 'subsample': 0.6}

In [24]:
xgbreg = XGBRegressor(nthreads=1,
                      colsample_bytree=1.0,
                      gamma=9.0,
                      learning_rate=0.5,
                      max_depth=128,
                      min_child_weight=60,
                      n_estimators=10,
                      reg_alpha=100,
                      subsample=0.85)

xgbreg.fit(x, y)
z = xgbreg.predict(x)
mychart(x, y, z)                      
                      